In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import pandas as pd
import scipy.stats as st
import scipy.integrate as integrate
from sklearn import linear_model
import statsmodels.discrete.discrete_model as sdm

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

In [ ]:
figsize = (12,7)
sns_colors = sns.color_palette()

## Обобщённые линейные модели

In [ ]:
from sklearn.preprocessing import OneHotEncoder
import statsmodels.api as sm

ss = [ s.strip().split() for s in open("apprentice.dat") ]
names = np.array([" ".join(x[:-5]) for x in ss])
d = np.array([[float(y) for y in x[-5:]] for x in ss])
X = np.hstack([ d[:, [0, 2, 3]], OneHotEncoder().fit_transform(d[:, 4].reshape(-1, 1)).toarray() ])
y = np.array(d[:, 1])

In [ ]:
ss

In [ ]:
lmb1 = np.mean(y)
lmb2 = np.mean(y[1:])

In [ ]:
lmb1, lmb2

In [ ]:
fig = plt.figure(figsize=(figsize[0], figsize[1]/2))
ax = fig.add_subplot(111)
xs = np.arange(0, 250)
ax.hist(y, bins=226, linewidth=0.1, density=True, color=sns_colors[0], alpha=0.5, label="Данные")
ax.plot(xs, st.poisson.pmf(xs, lmb1), color=sns_colors[1], linewidth=1.5, label="Распределение Пуассона")
ax.plot(xs, st.poisson.pmf(xs, lmb2), color=sns_colors[2], linewidth=1.5, label="Распределение Пуассона без выброса")

ax.legend(loc="upper right", fontsize=legend_fontsize)
ax.set_xlim(0, 225)

In [ ]:
data = np.log(X[:, 0])
xmax, xs = np.max(data)+.5, np.arange(1, np.max(data)+1, 0.05)
model_poisson = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.Poisson()).fit()
print(model_poisson.summary())
fig = plt.figure(figsize=(figsize[0], figsize[1]/1.5))
ax = fig.add_subplot(111)
preds = model_poisson.predict(sm.add_constant(xs, prepend=True))
ax.scatter(data, y, color=sns_colors[0], label="Данные")
ax.plot(xs, preds, color=sns_colors[1], linewidth=1.5, label="Пуассоновская регрессия по логарифму расстояния")
ax.legend(loc="upper right", fontsize=legend_fontsize)
ax.set_xlabel("Логарифм расстояния до Эдинбурга")
ax.set_xlim(3, xmax)
ax.set_ylim(0, np.max(y)+10)

In [ ]:
data = np.log(X[:, 1]*1000)
xmax, xs = np.max(data), np.arange(0.1, np.max(data)+.3, 0.05)
model_poisson = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.Poisson()).fit()
print(model_poisson.summary())
fig = plt.figure(figsize=(figsize[0], figsize[1]/1.5))
ax = fig.add_subplot(111)
preds = model_poisson.predict(sm.add_constant(xs, prepend=True))
ax.scatter(data, y, color=sns_colors[0], label="Данные")
ax.plot(xs, preds, color=sns_colors[1], linewidth=1.5, label="Пуассоновская регрессия по логарифму населения")
ax.legend(loc="upper left", fontsize=legend_fontsize)
ax.set_xlabel("Логарифм населения региона")
ax.set_xlim(np.min(data)-.25, xmax+.25)

In [ ]:
data = np.hstack([np.log(X[:,0]).reshape(-1, 1), np.log(X[:,1]*1000).reshape(-1, 1), np.log(X[:,2] / (100 - X[:,2])).reshape(-1, 1), X[:,3:]])
Xdf = pd.DataFrame(data,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South"])
model_poisson = sm.GLM(y, sm.add_constant(Xdf, prepend=True), family=sm.families.Poisson())
res = model_poisson.fit()
print(res.summary())

In [ ]:
data2 = np.hstack( [data, data[:, 3:] * data[:, 0].reshape(-1, 1)] )
Xdf = pd.DataFrame(data2,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South", "Log dist North", "Log dist West", "Log dist South"])
model_poisson = sm.GLM(y, sm.add_constant(Xdf, prepend=True), family=sm.families.Poisson())
res = model_poisson.fit()
print(res.summary())

In [ ]:
data2 = np.hstack( [data, data[:, 3:] * data[:, 0].reshape(-1, 1), data[:, 3:] * data[:, 1].reshape(-1, 1)] )
Xdf = pd.DataFrame(data2,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South", "Log dist North", "Log dist West", "Log dist South", "Log pop North", "Log pop West", "Log pop South"])
model_poisson = sm.GLM(y, sm.add_constant(Xdf, prepend=True), family=sm.families.Poisson())
res = model_poisson.fit()
print(res.summary())

In [ ]:
data2 = np.hstack( [data, data[:, 3:] * data[:, 0].reshape(-1, 1), data[:, 3:] * data[:, 1].reshape(-1, 1), data[:, 3:] * data[:, 2].reshape(-1, 1)] )
Xdf = pd.DataFrame(data2,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South", "Log dist North", "Log dist West", "Log dist South", "Log pop North", "Log pop West", "Log pop South", "Logit urb North", "Logit urb West", "Logit urb South"])
model_poisson = sm.GLM(y, sm.add_constant(Xdf, prepend=True), family=sm.families.Poisson())
res = model_poisson.fit()
print(res.summary())

In [ ]:
from sklearn.model_selection import train_test_split

def one_experiment(X, y, get_datadf):
    X_train, X_test, y_train, y_test =  train_test_split(X, y, test_size=0.1)
    model_poisson = sm.GLM(y_train, get_datadf(X_train), family=sm.families.Poisson()).fit()
    predictions = model_poisson.predict(get_datadf(X_test))
    return np.sqrt(np.mean((predictions - y_test) ** 2))

In [ ]:
def data_id(data):
    return data

def data_linear(data):
    return pd.DataFrame(data,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South"])

def data_distance(data):
    x = np.hstack( [data, data[:, 3:] * data[:, 0].reshape(-1, 1) ] )
    return pd.DataFrame(x,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South", "Log dist North", "Log dist West", "Log dist South"])

def data_all_interactions(data):
    x = np.hstack( [data, data[:, 3:] * data[:, 0].reshape(-1, 1), data[:, 3:] * data[:, 1].reshape(-1, 1), data[:, 3:] * data[:, 2].reshape(-1, 1)] )
    return pd.DataFrame(x,
                   columns=["Log distance", "Log population", "Logit urbanization", "North", "West", "South", "Log dist North", "Log dist West", "Log dist South", "Log pop North", "Log pop West", "Log pop South", "Logit urb North", "Logit urb West", "Logit urb South"])

In [ ]:
np.mean( [ one_experiment(data[:, :1], y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment(data[:, :2], y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment(data, y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment(data, y, data_distance) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment(data, y, data_linear) for _ in range(1000) ] )

In [ ]:
nb = sdm.NegativeBinomial(y, np.ones_like(y)).fit()
nb2 = sdm.NegativeBinomial(y[1:], np.ones_like(y[1:])).fit()

def nb_params(model):
    mu = np.exp(model.params[0])
    p = 1 / (1 + mu * model.params[1])
    n = mu * p / (1 - p)
    return n, p, mu

n, p, mu = nb_params(nb)
n2, p2, mu2 = nb_params(nb2)

In [ ]:
fig = plt.figure(figsize=(figsize[0], figsize[1]/2))
ax = fig.add_subplot(111)
xs = np.arange(0, 250)
ax.hist(y, bins=226, linewidth=0.1, density=True, color=sns_colors[0], alpha=0.5, label="Данные")
ax.plot(xs, st.nbinom.pmf(xs, n, p), color=sns_colors[1], linewidth=1.5, label="Отрицательное биномиальное распределение")
ax.plot(xs, st.nbinom.pmf(xs, n2, p2), color=sns_colors[2], linewidth=1.5, label="Отрицательное биномиальное распределение без выброса")

ax.legend(loc="upper right", fontsize=legend_fontsize)
ax.set_xlim(0, 225)

In [ ]:
data = np.log(X[:, 0])
xmax, xs = np.max(data)+.5, np.arange(1, np.max(data)+1, 0.05)
model_poisson = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.Poisson()).fit()
model_nb = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.NegativeBinomial()).fit()
print(model_nb.summary())
fig = plt.figure(figsize=(figsize[0], figsize[1]/1.5))
ax = fig.add_subplot(111)
preds = model_poisson.predict(sm.add_constant(xs, prepend=True))
preds_nb = model_nb.predict(sm.add_constant(xs, prepend=True))
ax.scatter(data, y, color=sns_colors[0], label="Данные")
ax.plot(xs, preds, color=sns_colors[1], linewidth=1.5, label="Пуассоновская регрессия по логарифму расстояния")
ax.plot(xs, preds_nb, color=sns_colors[2], linewidth=1.5, label="Отрицательная биномиальная регрессия по логарифму расстояния")
ax.legend(loc="upper right", fontsize=legend_fontsize)
ax.set_xlabel("Логарифм расстояния до Эдинбурга")
ax.set_xlim(3, xmax)
ax.set_ylim(0, np.max(y)+10)

In [ ]:
data = np.log(X[:, 1]*1000)
xmax, xs = np.max(data), np.arange(0.1, np.max(data)+.3, 0.05)
model_poisson = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.Poisson()).fit()
model_nb = sm.GLM(y, sm.add_constant(data, prepend=True), family=sm.families.NegativeBinomial(alpha=1.0)).fit()
print(model_poisson.summary())
fig = plt.figure(figsize=(figsize[0], figsize[1]/1.5))
ax = fig.add_subplot(111)
preds = model_poisson.predict(sm.add_constant(xs, prepend=True))
preds_nb = model_nb.predict(sm.add_constant(xs, prepend=True))
ax.scatter(data, y, color=sns_colors[0], label="Данные")
ax.plot(xs, preds, color=sns_colors[1], linewidth=1.5, label="Пуассоновская регрессия по логарифму населения")
ax.plot(xs, preds_nb, color=sns_colors[2], linewidth=1.5, label="Отрицательная биномиальная регрессия по логарифму расстояния")
ax.legend(loc="upper left", fontsize=legend_fontsize)
ax.set_xlabel("Логарифм населения региона")
ax.set_xlim(np.min(data)-.25, xmax+.25)

In [ ]:
def one_experiment_nb(X, y, get_datadf):
    X_train, X_test, y_train, y_test =  train_test_split(X, y, test_size=0.1)
    model_poisson = sm.GLM(y_train, get_datadf(X_train), family=sm.families.NegativeBinomial(alpha=1.0)).fit()
    predictions = model_poisson.predict(get_datadf(X_test))
    return np.sqrt(np.mean((predictions - y_test) ** 2))

In [ ]:
data = np.hstack([np.log(X[:,0]).reshape(-1, 1), np.log(X[:,1]*1000).reshape(-1, 1), np.log(X[:,2] / (100 - X[:,2])).reshape(-1, 1), X[:,3:]])

In [ ]:
np.mean( [ one_experiment_nb(data[:, :1], y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment_nb(data[:, :2], y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment_nb(data, y, data_id) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment_nb(data, y, data_distance) for _ in range(5000) ] )

In [ ]:
np.mean( [ one_experiment_nb(data, y, data_linear) for _ in range(1000) ] )